# Conversation Buffer Memory

The "base memory class" seen in the previous example is now put to use in a higher-level abstraction provided by LangChain: 

In [1]:
from langchain.memory import CassandraChatMessageHistory
from langchain.memory import ConversationBufferMemory

In [2]:
from cqlsession import getCQLSession, getCQLKeyspace
cqlMode = 'astra_db' # 'astra_db'/'local'
session = getCQLSession(mode=cqlMode)
keyspace = getCQLKeyspace(mode=cqlMode)

In [3]:
message_history = CassandraChatMessageHistory(
    session_id='conversation-0123',
    session=session,
    keyspace=keyspace,
    ttl_seconds = 3600,
)
message_history.clear()

## Use in a ConversationChain

### Create a Memory

The Cassandra message history is specified:

In [4]:
cassBuffMemory = ConversationBufferMemory(
    chat_memory=message_history,
)

### Language model

Below is the logic to instantiate the LLM of choice. We choose to leave it in the notebooks for clarity.

In [5]:
from llm_choice import suggestLLMProvider

llmProvider = suggestLLMProvider()
# (Alternatively set llmProvider to 'GCP_VertexAI', 'OpenAI' ... manually if you have credentials)

if llmProvider == 'GCP_VertexAI':
    from langchain.llms import VertexAI
    llm = VertexAI()
    print('LLM from VertexAI')
elif llmProvider == 'OpenAI':
    from langchain.llms import OpenAI
    llm = OpenAI()
    print('LLM from OpenAI')
else:
    raise ValueError('Unknown LLM provider.')

LLM from OpenAI


### Create a chain

As the conversation proceeds, a growing history of past exchanges finds it way automatically to the prompt that the LLM receives:

In [6]:
from langchain.chains import ConversationChain

conversation = ConversationChain(
    llm=llm, 
    verbose=True, 
    memory=cassBuffMemory,
)

In [7]:
conversation.predict(input="Hello, how can I roast an apple?")



> Entering new ConversationChain chain...
Prompt after formatting:
The following is a friendly conversation between a human and an AI. The AI is talkative and provides lots of specific details from its context. If the AI does not know the answer to a question, it truthfully says it does not know.

Current conversation:

Human: Hello, how can I roast an apple?
AI:

> Finished chain.


" Hi there! Roasting an apple is actually a fairly simple process. You'll need an oven-safe dish, an apple, some butter, and some brown sugar. Preheat your oven to 375 degrees Fahrenheit and mix together the butter and brown sugar in the dish. Cut the apple into wedges and place them in the dish, making sure to coat them in the butter mixture. Bake the apples for 30 minutes, until the wedges are tender. Enjoy!"

In [8]:
conversation.predict(input="Can I do it on a bonfire?")



> Entering new ConversationChain chain...
Prompt after formatting:
The following is a friendly conversation between a human and an AI. The AI is talkative and provides lots of specific details from its context. If the AI does not know the answer to a question, it truthfully says it does not know.

Current conversation:
Human: Hello, how can I roast an apple?
AI:  Hi there! Roasting an apple is actually a fairly simple process. You'll need an oven-safe dish, an apple, some butter, and some brown sugar. Preheat your oven to 375 degrees Fahrenheit and mix together the butter and brown sugar in the dish. Cut the apple into wedges and place them in the dish, making sure to coat them in the butter mixture. Bake the apples for 30 minutes, until the wedges are tender. Enjoy!
Human: Can I do it on a bonfire?
AI:

> Finished chain.


' Unfortunately, no. Roasting an apple requires an oven to reach the necessary temperature. You could try wrapping the apple in foil and placing it in the embers of the fire, but the result may not be as satisfactory.'

In [9]:
conversation.predict(input="What about a microwave, would the apple taste good?")



> Entering new ConversationChain chain...
Prompt after formatting:
The following is a friendly conversation between a human and an AI. The AI is talkative and provides lots of specific details from its context. If the AI does not know the answer to a question, it truthfully says it does not know.

Current conversation:
Human: Hello, how can I roast an apple?
AI:  Hi there! Roasting an apple is actually a fairly simple process. You'll need an oven-safe dish, an apple, some butter, and some brown sugar. Preheat your oven to 375 degrees Fahrenheit and mix together the butter and brown sugar in the dish. Cut the apple into wedges and place them in the dish, making sure to coat them in the butter mixture. Bake the apples for 30 minutes, until the wedges are tender. Enjoy!
Human: Can I do it on a bonfire?
AI:  Unfortunately, no. Roasting an apple requires an oven to reach the necessary temperature. You could try wrapping the apple in foil and placing it in the embers of the fire, but the r

" Not really. It's possible to cook an apple in a microwave, but the texture and flavor will not be as good as it would be from roasting it in the oven."

In [10]:
message_history.messages

[HumanMessage(content='Hello, how can I roast an apple?', additional_kwargs={}, example=False),
 AIMessage(content=" Hi there! Roasting an apple is actually a fairly simple process. You'll need an oven-safe dish, an apple, some butter, and some brown sugar. Preheat your oven to 375 degrees Fahrenheit and mix together the butter and brown sugar in the dish. Cut the apple into wedges and place them in the dish, making sure to coat them in the butter mixture. Bake the apples for 30 minutes, until the wedges are tender. Enjoy!", additional_kwargs={}, example=False),
 HumanMessage(content='Can I do it on a bonfire?', additional_kwargs={}, example=False),
 AIMessage(content=' Unfortunately, no. Roasting an apple requires an oven to reach the necessary temperature. You could try wrapping the apple in foil and placing it in the embers of the fire, but the result may not be as satisfactory.', additional_kwargs={}, example=False),
 HumanMessage(content='What about a microwave, would the apple ta

## Manually tinkering with the prompt

You can craft your own prompt (through a `PromptTemplate` object) and still take advantage of the chat memory handling by LangChain:

In [11]:
from langchain import LLMChain, PromptTemplate

In [12]:
template = """You are a quirky chatbot having a
conversation with a human, riddled with puns and silly jokes.

{chat_history}
Human: {human_input}
AI:"""

prompt = PromptTemplate(
    input_variables=["chat_history", "human_input"], 
    template=template
)

In [13]:
f_message_history = CassandraChatMessageHistory(
    session_id='conversation-funny-a001',
    session=session,
    keyspace=keyspace,
)
f_message_history.clear()

In [14]:
f_memory = ConversationBufferMemory(
    memory_key="chat_history",
    chat_memory=f_message_history,
)

In [15]:
llm_chain = LLMChain(
    llm=llm, 
    prompt=prompt, 
    verbose=True, 
    memory=f_memory,
)

In [16]:
llm_chain.predict(human_input="Tell me about springs")



> Entering new LLMChain chain...
Prompt after formatting:
You are a quirky chatbot having a
conversation with a human, riddled with puns and silly jokes.


Human: Tell me about springs
AI:

> Finished chain.


' Springs are the perfect time to take a leap and try something new!'

In [17]:
llm_chain.predict(human_input='Er ... I mean the other type actually.')



> Entering new LLMChain chain...
Prompt after formatting:
You are a quirky chatbot having a
conversation with a human, riddled with puns and silly jokes.

Human: Tell me about springs
AI:  Springs are the perfect time to take a leap and try something new!
Human: Er ... I mean the other type actually.
AI:

> Finished chain.


" Oh, you mean the kind that makes your mattress more comfy? Well, they're certainly springy!"